<a href="https://colab.research.google.com/github/ClaraFontes/projeto_ia/blob/main/Projeto_TEIA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Equipe:**
- Ana Clara Fontes
- Heitor Negromonte
- Matheus Felipe

# Análise da base de dados

In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip3 install torch torchvision torchaudio

In [ ]:
!pip install -U ydata-profiling

In [ ]:
from ydata_profiling import ProfileReport

In [ ]:
import pandas as pd
df_airbnb = pd.read_csv('/content/drive/MyDrive/PROJETO_TEIA/base/listings.csv')
print(df_airbnb.head())

        id                           listing_url       scrape_id last_scraped  \
0   241032   https://www.airbnb.com/rooms/241032  20160104002432   2016-01-04   
1   953595   https://www.airbnb.com/rooms/953595  20160104002432   2016-01-04   
2  3308979  https://www.airbnb.com/rooms/3308979  20160104002432   2016-01-04   
3  7421966  https://www.airbnb.com/rooms/7421966  20160104002432   2016-01-04   
4   278830   https://www.airbnb.com/rooms/278830  20160104002432   2016-01-04   

                                  name  \
0         Stylish Queen Anne Apartment   
1   Bright & Airy Queen Anne Apartment   
2  New Modern House-Amazing water view   
3                   Queen Anne Chateau   
4       Charming craftsman 3 bdm house   

                                             summary  \
0                                                NaN   
1  Chemically sensitive? We've removed the irrita...   
2  New modern house built in 2013.  Spectacular s...   
3  A charming apartment that sits at

In [ ]:
print("Dataset original: ",df_airbnb.shape)

Dataset original:  (3818, 92)


In [ ]:
# Lista das colunas consideradas importantes para a predição do preço
selected_columns = [
    'property_type', 'room_type', 'accommodates', 'bathrooms',
    'bedrooms', 'beds', 'bed_type', 'amenities', 'minimum_nights',
    'availability_365', 'number_of_reviews', 'review_scores_rating',
    'latitude', 'longitude', 'neighbourhood_cleansed'
]

# Definindo entrada e saída
X = df_airbnb[selected_columns]
y = df_airbnb['price']

print("Features (X):")
print(X.head())
print("\nVariável Alvo (y):")
print(y.head())

Features (X):
  property_type        room_type  accommodates  bathrooms  bedrooms  beds  \
0     Apartment  Entire home/apt             4        1.0       1.0   1.0   
1     Apartment  Entire home/apt             4        1.0       1.0   1.0   
2         House  Entire home/apt            11        4.5       5.0   7.0   
3     Apartment  Entire home/apt             3        1.0       0.0   2.0   
4         House  Entire home/apt             6        2.0       3.0   3.0   

   bed_type                                          amenities  \
0  Real Bed  {TV,"Cable TV",Internet,"Wireless Internet","A...   
1  Real Bed  {TV,Internet,"Wireless Internet",Kitchen,"Free...   
2  Real Bed  {TV,"Cable TV",Internet,"Wireless Internet","A...   
3  Real Bed  {Internet,"Wireless Internet",Kitchen,"Indoor ...   
4  Real Bed  {TV,"Cable TV",Internet,"Wireless Internet",Ki...   

   minimum_nights  availability_365  number_of_reviews  review_scores_rating  \
0               1               346           

In [ ]:
print("Dataset após seleção de colunas: ",X.shape)

Dataset após seleção de colunas:  (3818, 15)


In [ ]:
# Verificando valores nulos na saída
print(y.isnull().sum())

0


# Pandas Profiling

In [ ]:
airbnb_profile = ProfileReport(X)
airbnb_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Tratamento dos dados

In [ ]:
y

0        $85.00
1       $150.00
2       $975.00
3       $100.00
4       $450.00
         ...   
3813    $359.00
3814     $79.00
3815     $93.00
3816     $99.00
3817     $87.00
Name: price, Length: 3818, dtype: object

In [ ]:
# Tratando a coluna `price`
y = y.str.replace('$', '').str.replace(',', '').astype(float)
y

0        85.0
1       150.0
2       975.0
3       100.0
4       450.0
        ...  
3813    359.0
3814     79.0
3815     93.0
3816     99.0
3817     87.0
Name: price, Length: 3818, dtype: float64

In [ ]:
from sklearn.model_selection import train_test_split

# DIVISÃO EM TREINO E TESTE 20% para teste e 80% para treino
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

## Imputação de dados



In [ ]:
# Verificando dados nulos antes da imputação em cada conjunto
print("Valores nulos no conjunto de treino:")
print(X_train.isnull().sum())

print("\nValores nulos no conjunto de teste:")
print(X_test.isnull().sum())

Valores nulos no conjunto de treino:
property_type               1
room_type                   0
accommodates                0
bathrooms                  14
bedrooms                    5
beds                        1
bed_type                    0
amenities                   0
minimum_nights              0
availability_365            0
number_of_reviews           0
review_scores_rating      522
latitude                    0
longitude                   0
neighbourhood_cleansed      0
dtype: int64

Valores nulos no conjunto de teste:
property_type               0
room_type                   0
accommodates                0
bathrooms                   2
bedrooms                    1
beds                        0
bed_type                    0
amenities                   0
minimum_nights              0
availability_365            0
number_of_reviews           0
review_scores_rating      125
latitude                    0
longitude                   0
neighbourhood_cleansed      0
dtype: int64


### Colunas numéricas

In [ ]:
from sklearn.impute import SimpleImputer

# 1. Imputação para colunas numéricas
colunas_numericas = ['bathrooms', 'beds', 'bedrooms', 'review_scores_rating']

# Criar imputador para valores numéricos com a estratégia de mediana
imputer_numerico = SimpleImputer(strategy='median')

# Ajustar o imputador ao conjunto de treino e transformar
X_train[colunas_numericas] = imputer_numerico.fit_transform(X_train[colunas_numericas])

# Aplicar a transformação ao conjunto de teste
X_test[colunas_numericas] = imputer_numerico.transform(X_test[colunas_numericas])

print("Valores nulos no conjunto de treino:")
print(X_train.isnull().sum())

print("\nValores nulos no conjunto de teste:")
print(X_test.isnull().sum())

Valores nulos no conjunto de treino:
property_type             1
room_type                 0
accommodates              0
bathrooms                 0
bedrooms                  0
beds                      0
bed_type                  0
amenities                 0
minimum_nights            0
availability_365          0
number_of_reviews         0
review_scores_rating      0
latitude                  0
longitude                 0
neighbourhood_cleansed    0
dtype: int64

Valores nulos no conjunto de teste:
property_type             0
room_type                 0
accommodates              0
bathrooms                 0
bedrooms                  0
beds                      0
bed_type                  0
amenities                 0
minimum_nights            0
availability_365          0
number_of_reviews         0
review_scores_rating      0
latitude                  0
longitude                 0
neighbourhood_cleansed    0
dtype: int64


### Coluna categórica

In [ ]:
# 2. Imputação para colunas categóricas
colunas_categoricas = ['property_type']

# Criar imputador para valores categóricos com a estratégia de moda
imputer_categorico = SimpleImputer(strategy='most_frequent')

# Ajustar o imputador ao conjunto de treino e transformar
X_train[colunas_categoricas] = imputer_categorico.fit_transform(X_train[colunas_categoricas])

# Aplicar a transformação ao conjunto de teste
X_test[colunas_categoricas] = imputer_categorico.transform(X_test[colunas_categoricas])

# 3. Verificar valores nulos após imputação
print("Valores nulos no conjunto de treino:")
print(X_train.isnull().sum())

print("\nValores nulos no conjunto de teste:")
print(X_test.isnull().sum())

Valores nulos no conjunto de treino:
property_type             0
room_type                 0
accommodates              0
bathrooms                 0
bedrooms                  0
beds                      0
bed_type                  0
amenities                 0
minimum_nights            0
availability_365          0
number_of_reviews         0
review_scores_rating      0
latitude                  0
longitude                 0
neighbourhood_cleansed    0
dtype: int64

Valores nulos no conjunto de teste:
property_type             0
room_type                 0
accommodates              0
bathrooms                 0
bedrooms                  0
beds                      0
bed_type                  0
amenities                 0
minimum_nights            0
availability_365          0
number_of_reviews         0
review_scores_rating      0
latitude                  0
longitude                 0
neighbourhood_cleansed    0
dtype: int64


## Tratando dados categóricos

### One-hot Encoder

In [ ]:
from sklearn.preprocessing import OneHotEncoder

# Aplicando One-hot Encoding nas colunas categóricas com poucas categorias
# 'room_type' (3 categorias) e 'bed_type' (5 categorias)

categorical_features = ['room_type', 'bed_type']
encoder = OneHotEncoder(drop='first', sparse_output=False)

# Ajustar no conjunto de treino
encoded_train = encoder.fit_transform(X_train[categorical_features])

# Aplicar no conjunto de teste
encoded_test = encoder.transform(X_test[categorical_features])

In [ ]:
# Convertendo dados codificados para DataFrame
encoded_train_df = pd.DataFrame(
    encoded_train,
    columns=encoder.get_feature_names_out(categorical_features),
    index=X_train.index
)
encoded_test_df = pd.DataFrame(
    encoded_test,
    columns=encoder.get_feature_names_out(categorical_features),
    index=X_test.index
)

# Removendo as colunas originais e concatenando as novas colunas codificadas
X_train = X_train.drop(columns=categorical_features)
X_test = X_test.drop(columns=categorical_features)

X_train = pd.concat([X_train, encoded_train_df], axis=1)
X_test = pd.concat([X_test, encoded_test_df], axis=1)

In [ ]:
# Atualizan as 'selected_columns' com as novas colunas
selected_columns = [col for col in selected_columns if col not in categorical_features]
encoded_columns = list(encoder.get_feature_names_out(categorical_features))
selected_columns.extend(encoded_columns)

# Verificar os resultados
print("Novas colunas adicionadas pelas categorias codificadas:")
print(encoded_columns)
print("\nColunas atualizadas em selected_columns:")
print(selected_columns)

# Validar a nova forma dos conjuntos de dados
print("\nTamanho do conjunto de treino: ", X_train.shape)
print("Tamanho do conjunto de teste: ", X_test.shape)

Novas colunas adicionadas pelas categorias codificadas:
['room_type_Private room', 'room_type_Shared room', 'bed_type_Couch', 'bed_type_Futon', 'bed_type_Pull-out Sofa', 'bed_type_Real Bed']

Colunas atualizadas em selected_columns:
['property_type', 'accommodates', 'bathrooms', 'bedrooms', 'beds', 'amenities', 'minimum_nights', 'availability_365', 'number_of_reviews', 'review_scores_rating', 'latitude', 'longitude', 'neighbourhood_cleansed', 'room_type_Private room', 'room_type_Shared room', 'bed_type_Couch', 'bed_type_Futon', 'bed_type_Pull-out Sofa', 'bed_type_Real Bed']

Tamanho do conjunto de treino:  (3054, 19)
Tamanho do conjunto de teste:  (764, 19)


### Target Encoder

In [ ]:
# Aplicando One-hot Encoding nas colunas categóricas com muitas categorias
# 'neighbourhood_cleansed' e 'property_type'

# Função para aplicar Target Encoding
def target_encode(train_col, target, test_col):
    # Dicionário com as médias das categorias no conjunto de treino
    category_means = train_col.groupby(train_col).apply(lambda x: target[x.index].mean()).to_dict()

    # Substituir as categorias pelo valor médio da variável alvo (treino)
    train_encoded = train_col.map(category_means)

    # Substituir as categorias no conjunto de teste, utilizando os valores do treino
    test_encoded = test_col.map(category_means)

    # Tratar categorias desconhecidas no conjunto de teste
    test_encoded = test_encoded.fillna(target.mean())

    return train_encoded, test_encoded

# Aplicando Target Encoding nas colunas
for col in ['neighbourhood_cleansed', 'property_type']:
    X_train[col], X_test[col] = target_encode(X_train[col], y_train, X_test[col])

# Exibindo as primeiras linhas dos dados codificados
print("X_train após Target Encoding:")
print(X_train.head())
print()
print("X_test após Target Encoding:")
print(X_test.head())


X_train após Target Encoding:
      property_type  accommodates  bathrooms  bedrooms  beds  \
700      123.379056             1        1.0       1.0   1.0   
2045     132.896477             2        1.0       1.0   1.0   
644      132.896477             2        1.0       1.0   1.0   
2810     123.379056             3        1.0       1.0   1.0   
2206     132.896477             2        1.0       1.0   1.0   

                                              amenities  minimum_nights  \
700   {Internet,"Wireless Internet",Kitchen,"Elevato...               2   
2045  {Internet,"Wireless Internet","Free Parking on...               2   
644   {Internet,"Wireless Internet","Free Parking on...               1   
2810  {TV,Internet,"Wireless Internet","Wheelchair A...               1   
2206  {"Wireless Internet","Free Parking on Premises...               2   

      availability_365  number_of_reviews  review_scores_rating   latitude  \
700                185                  1               

### Tratando coluna 'Amenities'

A coluna amenities está em formato textual. Foi necessário tratá-la, sendo escolhida a abordagem de transformar esta coluna em uma contagem. Por exemplo: Se a propriedade está com o valor "{"Wireless Internet","Free Parking on Premises",Heating,"Smoke Detector",Essentials,Shampoo}", será transformado no valor 6.

In [ ]:
# Transformando a coluna amenities em uma contagem
# Treino
X_train['amenities'] = X_train['amenities'].str.replace('[{}"]', '', regex=True)  # Remover caracteres desnecessários
X_train['num_amenities'] = X_train['amenities'].str.split(',').apply(len)  # Contar número de amenidades

# Teste
X_test['amenities'] = X_test['amenities'].str.replace('[{}"]', '', regex=True)
X_test['num_amenities'] = X_test['amenities'].str.split(',').apply(len)

# Removendo a coluna original de 'amenities' após o processamento
X_train = X_train.drop(columns=['amenities'])
X_test = X_test.drop(columns=['amenities'])

print("X_train após processamento de amenities:")
print(X_train.head())

print("X_test após processamento de amenities:")
print(X_test.head())


X_train após processamento de amenities:
      property_type  accommodates  bathrooms  bedrooms  beds  minimum_nights  \
700      123.379056             1        1.0       1.0   1.0               2   
2045     132.896477             2        1.0       1.0   1.0               2   
644      132.896477             2        1.0       1.0   1.0               1   
2810     123.379056             3        1.0       1.0   1.0               1   
2206     132.896477             2        1.0       1.0   1.0               2   

      availability_365  number_of_reviews  review_scores_rating   latitude  \
700                185                  1                  80.0  47.659005   
2045               308                 24                  94.0  47.699719   
644                360                 78                  97.0  47.609264   
2810               365                 23                  93.0  47.618479   
2206               358                 12                  95.0  47.514652   

       lo

## Tratando dados numéricos com Standard Scaler

In [ ]:
from sklearn.preprocessing import StandardScaler

# Colunas numéricas a serem escalonadas
numerical_columns = [
    'property_type', 'accommodates', 'bathrooms', 'bedrooms',
    'beds', 'minimum_nights', 'availability_365',
    'number_of_reviews', 'review_scores_rating',
    'latitude', 'longitude', 'num_amenities'
]

scaler = StandardScaler()
scaler_y = StandardScaler()

# x treino
X_train_scaled = scaler.fit_transform(X_train[numerical_columns])
# x teste
X_test_scaled= scaler.transform(X_test[numerical_columns])
# y treino
y_train_scaled = scaler_y.fit_transform(y_train.values.reshape(-1, 1))
# y teste
y_test_scaled = scaler_y.transform(y_test.values.reshape(-1, 1))

# DataFrames
X_train_scaled_df = pd.DataFrame(X_train_scaled, columns=numerical_columns)
X_test_scaled_df = pd.DataFrame(X_test_scaled, columns=numerical_columns)
y_train_scaled = pd.Series(y_train_scaled.flatten(), name='price')
y_test_scaled = pd.Series(y_test_scaled.flatten(), name='price')

print("Conjunto de Treinamento Escalonado:")
print(X_train_scaled_df.head())

print("\nConjunto de Teste Escalonado:")
print(X_test_scaled_df.head())

print("\nSaída de Treinamento Escalonada:")
print(y_train_scaled.head())

print("\nSaída de Teste Escalonada:")
print(y_test_scaled.head())

Conjunto de Treinamento Escalonado:
   property_type  accommodates  bathrooms  bedrooms      beds  minimum_nights  \
0      -0.434379     -1.190519  -0.441437 -0.353436 -0.655632       -0.024048   
1       0.385722     -0.683286  -0.441437 -0.353436 -0.655632       -0.024048   
2       0.385722     -0.683286  -0.441437 -0.353436 -0.655632       -0.079020   
3      -0.434379     -0.176053  -0.441437 -0.353436 -0.655632       -0.079020   
4       0.385722     -0.683286  -0.441437 -0.353436 -0.655632       -0.024048   

   availability_365  number_of_reviews  review_scores_rating  latitude  \
0         -0.471197          -0.548257             -2.390446  0.701161   
1          0.496939           0.053726             -0.115462  1.644864   
2          0.906232           1.467077              0.372034 -0.451794   
3          0.945587           0.027553             -0.277961 -0.238202   
4          0.890490          -0.260352              0.047036 -2.644794   

   longitude  num_amenities  
0 

# Redes Neurais

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import mean_absolute_error, r2_score, mean_squared_error
import numpy as np

device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [ ]:
# Função para calcular métricas
def calculate_metrics(y_true, y_pred):
    y_true = y_true.cpu().numpy()
    y_pred = y_pred.cpu().numpy()
    mae = mean_absolute_error(y_true, y_pred)
    mse = mean_squared_error(y_true, y_pred)
    rmse = np.sqrt(mse)
    r2 = r2_score(y_true, y_pred)
    return mae, mse, rmse, r2

In [ ]:
# Criando as arquiteturas
class DenseModel(nn.Module):
    def __init__(self, input_dim, architecture):
        super(DenseModel, self).__init__()
        layers = []
        for i, (in_dim, out_dim) in enumerate(architecture):
            layers.append(nn.Linear(in_dim, out_dim))
            if i < len(architecture) - 1:  # Não adicionar ativação na última camada
                layers.append(nn.LeakyReLU())
                layers.append(nn.Dropout(0.3))
        self.network = nn.Sequential(*layers)

    def forward(self, x):
        return self.network(x)

In [ ]:
# Definindo arquiteturas
architectures = {
    "Modelo 1": [(X_train_scaled.shape[1], 32), (32, 16), (16, 1)],
    "Modelo 2": [(X_train_scaled.shape[1], 64), (64, 32), (32, 16), (16, 8), (8, 1)],
    "Modelo 3": [(X_train_scaled.shape[1], 128), (128, 64), (64, 1)],
}

In [ ]:
# Treinamento e avaliação
results = {}
epochs = 300
batch_size = 64

Valor das épocas foi atualizado para verificar possíveis melhorias nos resultados:

In [ ]:
results = {}
epochs = 400
batch_size = 64

In [ ]:
for model_name, arch in architectures.items():
    print(f"\nTreinando {model_name}...")
    model = DenseModel(X_train_scaled.shape[1], arch).to(device)
    criterion = nn.MSELoss()
    optimizer = optim.Adam(model.parameters(), weight_decay=1e-4)  # Regularização L2
    scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=10, factor=0.5)

    train_losses = []
    test_losses = []

    X_train_t = torch.tensor(X_train_scaled, dtype=torch.float32).to(device)
    X_test_t = torch.tensor(X_test_scaled, dtype=torch.float32).to(device)
    y_train_t = torch.tensor(y_train_scaled.values, dtype=torch.float32).unsqueeze(1).to(device)
    y_test_t = torch.tensor(y_test_scaled.values, dtype=torch.float32).unsqueeze(1).to(device)

    # Mini-batch training
    train_dataset = torch.utils.data.TensorDataset(X_train_t, y_train_t)
    train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

    for epoch in range(epochs):
        model.train()
        epoch_loss = 0
        for batch_X, batch_y in train_loader:
            optimizer.zero_grad()
            outputs = model(batch_X)
            loss = criterion(outputs, batch_y)
            loss.backward()
            optimizer.step()
            epoch_loss += loss.item()

        train_losses.append(epoch_loss / len(train_loader))

        # Avaliação
        model.eval()
        with torch.no_grad():
            outputs = model(X_test_t)
            test_loss = criterion(outputs, y_test_t).item()
            test_losses.append(test_loss)

        scheduler.step(test_loss)

        # Adicionando o log das perdas
        print(f"Epoch {epoch + 1}/{epochs}, Train Loss: {train_losses[-1]:.4f}, Test Loss: {test_loss:.4f}")

    # Métricas
    model.eval()
    with torch.no_grad():
        pred = model(X_test_t)
        mae, mse, rmse, r2 = calculate_metrics(y_test_t, pred)
        results[model_name] = {
            "MAE": mae,
            "MSE": mse,
            "RMSE": rmse,
            "R^2": r2,
            "Train Loss": train_losses,
            "Test Loss": test_losses
        }


Treinando Modelo 1...
Epoch 1/400, Train Loss: 0.9536, Test Loss: 0.8291
Epoch 2/400, Train Loss: 0.7835, Test Loss: 0.6378
Epoch 3/400, Train Loss: 0.6604, Test Loss: 0.5165
Epoch 4/400, Train Loss: 0.6083, Test Loss: 0.4915
Epoch 5/400, Train Loss: 0.6192, Test Loss: 0.4757
Epoch 6/400, Train Loss: 0.5425, Test Loss: 0.4605
Epoch 7/400, Train Loss: 0.5790, Test Loss: 0.4573
Epoch 8/400, Train Loss: 0.5613, Test Loss: 0.4489
Epoch 9/400, Train Loss: 0.5270, Test Loss: 0.4364
Epoch 10/400, Train Loss: 0.5590, Test Loss: 0.4370
Epoch 11/400, Train Loss: 0.5816, Test Loss: 0.4348
Epoch 12/400, Train Loss: 0.5271, Test Loss: 0.4316
Epoch 13/400, Train Loss: 0.5467, Test Loss: 0.4273
Epoch 14/400, Train Loss: 0.5169, Test Loss: 0.4224
Epoch 15/400, Train Loss: 0.4998, Test Loss: 0.4153
Epoch 16/400, Train Loss: 0.5059, Test Loss: 0.4174
Epoch 17/400, Train Loss: 0.5247, Test Loss: 0.4176
Epoch 18/400, Train Loss: 0.5115, Test Loss: 0.4139
Epoch 19/400, Train Loss: 0.5040, Test Loss: 0.410

In [ ]:
# Exibir resultados
results_df = pd.DataFrame(results).T
print("Resultados com 300 épocas:")
print('\n',results_df)

Resultados com 300 épocas:

                MAE       MSE      RMSE       R^2  \
Modelo 1  0.400899  0.393087  0.626967  0.605348   
Modelo 2  0.410464  0.404842  0.636272  0.593547   
Modelo 3  0.394689  0.377305  0.614251  0.621193   

                                                 Train Loss  \
Modelo 1  [0.9843303350110849, 0.7517619958768288, 0.629...   
Modelo 2  [1.0037266028424103, 0.8871753069882592, 0.710...   
Modelo 3  [0.6737946253269911, 0.5348287047818303, 0.492...   

                                                  Test Loss  
Modelo 1  [0.8318119049072266, 0.5868898630142212, 0.527...  
Modelo 2  [0.8853721618652344, 0.7209026217460632, 0.530...  
Modelo 3  [0.46531686186790466, 0.43960508704185486, 0.4...  


Esta parte do código foi rodada após a atualização da quantidade de épocas:

In [ ]:
# Exibir resultados
results_df = pd.DataFrame(results).T
print("Resultados com 400 épocas:")
print('\n',results_df)

Resultados com 400 épocas:

                MAE       MSE      RMSE       R^2  \
Modelo 1  0.401063  0.395554  0.628931  0.602872   
Modelo 2  0.402494  0.398782  0.631492  0.599631   
Modelo 3  0.393069  0.375929  0.613131  0.622574   

                                                 Train Loss  \
Modelo 1  [0.9536389460166296, 0.7834632763018211, 0.660...   
Modelo 2  [0.9545330132047335, 0.7132320913175741, 0.680...   
Modelo 3  [0.6956044336160024, 0.5352552408973376, 0.506...   

                                                  Test Loss  
Modelo 1  [0.8291242718696594, 0.6377785801887512, 0.516...  
Modelo 2  [0.7898210287094116, 0.5378513336181641, 0.539...  
Modelo 3  [0.46673232316970825, 0.4455110430717468, 0.43...  
